## 元論文

In [8]:
import numpy as np
import pandas as pd
from collections import defaultdict
import sys
import os

sys.path.append(os.path.abspath(".."))  # 1階層上を追加
import pulp_exc.scflp_v4 as scflp

In [10]:
instances = [
    {"I": 20,  "J": 20,  "p": 2, "r": 2},
    {"I": 20,  "J": 20,  "p": 3, "r": 2},
    {"I": 20,  "J": 20,  "p": 2, "r": 3},

    {"I": 40,  "J": 40,  "p": 2, "r": 2},
    {"I": 40,  "J": 40,  "p": 3, "r": 2},
    {"I": 40,  "J": 40,  "p": 2, "r": 3},

    {"I": 60,  "J": 60,  "p": 2, "r": 2},
    {"I": 60,  "J": 60,  "p": 3, "r": 2},
    {"I": 60,  "J": 60,  "p": 2, "r": 3},

    {"I": 80,  "J": 80,  "p": 2, "r": 2},
    {"I": 80,  "J": 80,  "p": 3, "r": 2},
    {"I": 80,  "J": 80,  "p": 2, "r": 3},

    {"I": 100, "J": 100, "p": 2, "r": 2},
    {"I": 100, "J": 100, "p": 3, "r": 2},
    {"I": 100, "J": 100, "p": 2, "r": 3},

    {"I": 200, "J": 200, "p": 2, "r": 2},
    {"I": 200, "J": 200, "p": 3, "r": 2},
    {"I": 200, "J": 200, "p": 2, "r": 3},

    {"I": 300, "J": 300, "p": 2, "r": 2},
    {"I": 300, "J": 300, "p": 3, "r": 2},
    {"I": 300, "J": 300, "p": 2, "r": 3},
]


In [11]:
base_seed = 20250909   # 任意の固定値（再現用）

In [12]:
def make_seed(inst_id: int, run: int, base: int = base_seed) -> int:
    """インスタンスIDと試行番号に依存した再現可能シード"""
    return int(np.random.SeedSequence([base, inst_id, run]).generate_state(1)[0])

In [22]:
instances = [


    {"I": 300, "J": 300, "p": 2, "r": 2},
    {"I": 300, "J": 300, "p": 3, "r": 2},
    {"I": 300, "J": 300, "p": 2, "r": 3},
]


In [ ]:
n_runs = 10
beta = 0.1

# Branch-and-Cut の既定（あなたが動かした設定に近い）
solver_kwargs = dict(
    max_nodes=1000,
    max_rounds_per_node=3,
    tol=1e-3,
    pulp_solver="CBC",
    node_selection="bestbound",   # "dfs" も可
    log_level="info",
    separation="approx",
    cut_policy="auto",
    lp_relax=True,                # LP緩和（推奨）
)


all_results = []

for inst_id, params in enumerate(instances, start=1):
    for run in range(n_runs):
        seed = make_seed(inst_id, run)
        data = scflp.make_random_instance(
            I=params["I"], J=params["J"], p=params["p"], r=params["r"],
            beta=beta, seed=seed
        )

        res = scflp.scflp_branch_and_cut(data, **solver_kwargs)

        # 1試行ぶんの記録
        row = {
            "instance_id": inst_id,
            "run": run,
            "I": params["I"], "J": params["J"], "p": params["p"], "r": params["r"],
            "beta": beta,
            # branch_and_cut の返り値に合わせる
            "theta": res.get("theta_best", None),
            "time_sec": res.get("time_sec", None),
            "status": res.get("status", None),
            "nodes_explored": res.get("nodes_explored", None),
            "gap_bound": res.get("gap_bound", None),
            "total_cuts": res.get("total_cuts", None),
            "total_bulge": res.get("total_bulge", None),
            "total_submod": res.get("total_submod", None),
            "x_best_sites": res.get("x_best", None)
        }
        all_results.append(row)

# DataFrame にまとめて CSV 保存
df = pd.DataFrame(all_results)

from datetime import datetime
out = f"scflp_results_all_{datetime.now().strftime('%Y%m%d_%H%M%S')}.csv"

df.to_csv(out, index=False, encoding="utf-8")
print(f"保存完了: {out}")

════════════════════════════════════════════════════════════════════════════════
🚀 Branch-and-Cut（論文 Algorithm 1）開始
════════════════════════════════════════════════════════════════════════════════
────────────────────────────────────────────────────────────────────────────────
➤ 🌿 ノード展開: depth=0, |fix1|=0, |fix0|=0
➤    · ノード(depth=0): θ̂=1.000000, L=0.377092, viol=6.229e-01
✂️  カット追加: SUBMOD
➤    · ノード(depth=0): θ̂=1.000000, L=0.501860, viol=4.981e-01
✂️  カット追加: SUBMOD
➤    · ノード(depth=0): θ̂=0.797053, L=0.541581, viol=2.555e-01
✂️  カット追加: BULGE
⚠️  このノードでのカット上限に到達。
➤ 🌱 分枝: j*=9 → 子ノード depth=1 を2つ追加
────────────────────────────────────────────────────────────────────────────────
➤ 🌿 ノード展開: depth=1, |fix1|=1, |fix0|=0
➤    · ノード(depth=1): θ̂=0.685479, L=0.522130, viol=1.633e-01
✂️  カット追加: BULGE
➤    · ノード(depth=1): θ̂=0.683223, L=0.509422, viol=1.738e-01
✂️  カット追加: BULGE
➤    · ノード(depth=1): θ̂=0.649718, L=0.530948, viol=1.188e-01
✂️  カット追加: BULGE
⚠️  このノードでのカット上限に到達。
➤ 🌱 分枝: j*=36 → 子

## 豊島

In [3]:
%run ../mutation_lambda/func.ipynb

In [ ]:
import numpy as np
import pandas as pd
import random, time

results = []
num_rows_columns = 50   # サイト配置グリッドの一辺
alpha = 0.0             # 固定
beta = 0.01
n_runs = 10             # 繰り返し回数
eta = 0.01       # 学習率

for inst_id, params in enumerate(instances, start=1):
    objs_relaxed, objs_binary, objs_ex, times = [], [], [], []

    for run in range(n_runs):
        seed = make_seed(inst_id, run)

        # 需要点の重みベクトル
        h_i = np.full(params["I"], 1 / params["I"])
        J_L = {}  # インデックスとして候補施設の一部を選択
        J_F = {}

        start = time.time()
        x_R, y_R, obj_relaxed, x_proj, y_proj, obj_binary, obj_ex, candidate_sites, demand_points, history = lgda_solver(
            params["I"], params["J"], num_rows_columns,
            params["p"], params["r"],
            alpha, beta, h_i, J_L, J_F,
            eta_x=eta, eta_y=eta, eta_lambda=eta,
            mu=.05,
            max_iter=200_000,
            tau_interval=10_000,
            return_history=True
        )
        elapsed = time.time() - start

        objs_relaxed.append(obj_relaxed)
        objs_binary.append(obj_binary)
        objs_ex.append(obj_ex)
        times.append(elapsed)
        print(f"  試行 {run+1}/{n_runs} 完了: obj_relaxed={obj_relaxed}, obj_binary={obj_binary}, obj_ex={obj_ex}, time_sec={elapsed}")

    # 各インスタンスの平均を保存
    row = {
        "I": params["I"],
        "J": params["J"],
        "p": params["p"],
        "r": params["r"],
        #"beta": beta,
        "obj_relaxed_avg": np.mean(objs_relaxed),
        "obj_binary_avg": np.mean(objs_binary),
        "obj_ex_avg": np.mean(objs_ex),
        "time_avg_sec": np.mean(times)
    }
    results.append(row)
    print(f"完了: instance_id={inst_id}, I={params['I']}, J={params['J']}, p={params['p']}, r={params['r']}")
    print(f"  obj_relaxed_avg={row['obj_relaxed_avg']}, obj_binary_avg={row['obj_binary_avg']}, obj_ex_avg={row['obj_ex_avg']}, time_avg_sec={row['time_avg_sec']}")



869923100
  試行 1/10 完了: obj_relaxed=0.5025954053114841, obj_binary=0.5021253607592974, obj_ex=0.5021253607592974, time_sec=103.30700850486755
4257549051
  試行 2/10 完了: obj_relaxed=0.5036377377662136, obj_binary=0.5035111834817034, obj_ex=0.5035111834817034, time_sec=98.57715797424316
2379752947
  試行 3/10 完了: obj_relaxed=0.5018335262820544, obj_binary=0.5018025467178752, obj_ex=0.5018025467178752, time_sec=98.55835700035095
561815908
  試行 4/10 完了: obj_relaxed=0.5006549205740147, obj_binary=0.5012047407978775, obj_ex=0.5012047407978775, time_sec=98.905433177948
4083333777
  試行 5/10 完了: obj_relaxed=0.5054067217418194, obj_binary=0.5050529965015254, obj_ex=0.5050529965015254, time_sec=98.65028309822083
2416227123
  試行 6/10 完了: obj_relaxed=0.5057917049675487, obj_binary=0.5048629788488672, obj_ex=0.5048629788488672, time_sec=99.20986557006836
1587348034
  試行 7/10 完了: obj_relaxed=0.5036577746549395, obj_binary=0.5032728784604109, obj_ex=0.503272878460411, time_sec=118.50354766845703
420749011

NameError: name 'datetime' is not defined

In [15]:
from datetime import datetime
# DataFrame 化 & CSV 保存
df = pd.DataFrame(results)
df.to_csv(f"lgda_results_avg_nomask_{datetime.now().strftime('%Y%m%d_%H%M%S')}.csv", index=False, encoding="utf-8")
print(df)
print("保存完了:",f"lgda_results_avg_nomask_{datetime.now().strftime('%Y%m%d_%H%M%S')}.csv")

      I    J  p  r  obj_relaxed_avg  obj_binary_avg  obj_ex_avg  time_avg_sec
0    20   20  2  2         0.503224        0.502963    0.502963    110.180982
1    20   20  3  2         0.602502        0.602329    0.602329    101.123391
2    20   20  2  3         0.404173        0.404031    0.404031     94.101886
3    40   40  2  2         0.502914        0.502577    0.502577     95.877918
4    40   40  3  2         0.602375        0.602257    0.602257     96.968829
5    40   40  2  3         0.402676        0.402182    0.402182     95.475764
6    60   60  2  2         0.501192        0.501109    0.501109     95.086523
7    60   60  3  2         0.601073        0.601168    0.601168     90.588306
8    60   60  2  3         0.401240        0.401112    0.401112     90.745860
9    80   80  2  2         0.500694        0.500917    0.500917     91.106397
10   80   80  3  2         0.599788        0.600275    0.600275     90.968194
11   80   80  2  3         0.401117        0.401047    0.401047 